In [1]:
import numpy as np
from docplex.cp.model import *
from docplex.mp.model import Model
from docplex.mp.constants import ObjectiveSense
from docplex.util.environment import get_environment

In [2]:
from io import StringIO 
import sys

class Capturing(list):
    def __enter__(self):
        self._stdout = sys.stdout
        sys.stdout = self._stringio = StringIO()
        return self
    def __exit__(self, *args):
        self.extend(self._stringio.getvalue().splitlines())
        del self._stringio    # free up some memory
        sys.stdout = self._stdout
def calc_obj(x,proc_t,return_max=True):
    #calc value of objective function
    if return_max:
        return max(np.array(np.transpose(x)).dot(np.array(proc_t)))
    return np.array(np.transpose(x)).dot(np.array(proc_t))

def solve(proc_t,nb_m):
    #params: processing times, number of machines 

    
    mdl = Model()
   
   
    #add bin decision variables
    x=[]
    
    for job_id in range(proc_t.shape[1]):
        x_row=[]
        for i in range(nb_m):
            curr_x=mdl.integer_var(0, 1,'a_%i_%i' %(job_id,i))
            x_row.append(curr_x)
        x.append(x_row)
    #add every job needs to be mapped to exactly one machine constraint
    for job_id in range(proc_t.shape[1]):
        mdl.add(mdl.sum([x[job_id][mach_id] for mach_id in range(nb_m)])==1)
    
  
   
        
    #calculate sum of all job durations for every machine
    obj_var=[mdl.sum(x[job_id][mach_id]*proc_t[mach_id][job_id] for job_id in range(proc_t.shape[1]))for mach_id in range(nb_m)]
   
    #minimize the max duration of all machines
    mdl.minimize(mdl.max(obj_var))
    import time
    start = time.time()
    mdl.parameters.threads = 8
    mdl.parameters.mip.tolerances.mipgap = 0.000001
    mdl.parameters.timelimit = 120  # nurse should not take more than that !
    msol=mdl.solve()
    if msol is not None:
        print("solution for a cost of {}".format(mdl.objective_value))
        print(mdl.print_solution())
      
        # print_solution(model)
        
    else:
        print("* model is infeasible")
        return None
    
   
    
    with Capturing() as output:
        mdl.print_solution()
    
        
   
    

        return output,mdl.objective_value,mdl.get_solve_status()

In [3]:
import re
def std_to_jm_mat(x,nbj,nbm):
    y=np.zeros((nbj,nbm),dtype=np.int32)
    for i in x[0][1:]:
        l=re.findall(r'\d+',i)
        
        y[int(l[0])][int(l[1])]=int(l[2])
    return y
def simulation(pt_mean,pt_std,nb_t_range,nb_m_range,nb_data,pt_int=False):
    # init parameters
    # pt_mean: mean of processtime (duration of task on every machine)
    # pt_std:std of processtime 
    # number of task range f.e. [2,10] means uniform distribution between 2 and 10 tasks
    # number of machine range f.e. [2,10] means uniform distribution between 2 and 10 machines
    # nb_data = number of datasamples which should get generated
    # pt_int = (boolean) if process time is int or float (default: False)
    # return_dur = process time get's return (for statistics, default:False)
    x=[]
    y=[]
    stat=[]
    
    for i in range(nb_data):
        
        nb_m=np.random.randint(nb_m_range[0],nb_m_range[1])
        nb_t=np.random.randint(nb_t_range[0],nb_t_range[1])
        
        print('it:',i,'\t#m:',nb_m,'\t#t:',nb_t)
        if pt_int:
            proc_t=np.random.normal(loc=pt_mean,scale=pt_std,size=(nb_m,nb_t))
            proc_t=proc_t.astype(np.int64)
        else:
            proc_t=np.random.normal(loc=pt_mean,scale=pt_std,size=(nb_m,nb_t))
          
        x.append(proc_t)
        
        sol=solve(proc_t,proc_t.shape[0])
        y.append(std_to_jm_mat(np.array(sol),nb_t,nb_m))
        print(sol)
        stat.append(sol[2])
       
        
    
       
    return x,y,stat


In [10]:
#x=simulation(30,7,[5,6],[2,3],1,True)   
x,y,stat=simulation(30,7,[40,41],[5,6],5000,True)
x

it: 0 	#m: 5 	#t: 40
solution for a cost of 182
objective: 182
  a_0_4=1
  a_1_1=1
  a_2_3=1
  a_3_2=1
  a_4_0=1
  a_5_0=1
  a_6_3=1
  a_7_4=1
  a_8_1=1
  a_9_0=1
  a_10_4=1
  a_11_3=1
  a_12_2=1
  a_13_3=1
  a_14_0=1
  a_15_0=1
  a_16_0=1
  a_17_4=1
  a_18_0=1
  a_19_4=1
  a_20_1=1
  a_21_1=1
  a_22_2=1
  a_23_3=1
  a_24_4=1
  a_25_1=1
  a_26_3=1
  a_27_2=1
  a_28_0=1
  a_29_4=1
  a_30_2=1
  a_31_4=1
  a_32_1=1
  a_33_2=1
  a_34_1=1
  a_35_2=1
  a_36_3=1
  a_37_2=1
  a_38_1=1
  a_39_2=1
None
(['objective: 182', '  a_0_4=1', '  a_1_1=1', '  a_2_3=1', '  a_3_2=1', '  a_4_0=1', '  a_5_0=1', '  a_6_3=1', '  a_7_4=1', '  a_8_1=1', '  a_9_0=1', '  a_10_4=1', '  a_11_3=1', '  a_12_2=1', '  a_13_3=1', '  a_14_0=1', '  a_15_0=1', '  a_16_0=1', '  a_17_4=1', '  a_18_0=1', '  a_19_4=1', '  a_20_1=1', '  a_21_1=1', '  a_22_2=1', '  a_23_3=1', '  a_24_4=1', '  a_25_1=1', '  a_26_3=1', '  a_27_2=1', '  a_28_0=1', '  a_29_4=1', '  a_30_2=1', '  a_31_4=1', '  a_32_1=1', '  a_33_2=1', '  a_34_1=1', ' 

solution for a cost of 175
objective: 175
  a_0_1=1
  a_1_1=1
  a_2_1=1
  a_3_2=1
  a_4_1=1
  a_5_1=1
  a_6_3=1
  a_7_2=1
  a_8_4=1
  a_9_0=1
  a_10_4=1
  a_11_3=1
  a_12_0=1
  a_13_3=1
  a_14_4=1
  a_15_1=1
  a_16_0=1
  a_17_2=1
  a_18_2=1
  a_19_2=1
  a_20_3=1
  a_21_2=1
  a_22_0=1
  a_23_3=1
  a_24_0=1
  a_25_4=1
  a_26_0=1
  a_27_1=1
  a_28_3=1
  a_29_4=1
  a_30_0=1
  a_31_4=1
  a_32_2=1
  a_33_2=1
  a_34_1=1
  a_35_4=1
  a_36_2=1
  a_37_0=1
  a_38_0=1
  a_39_3=1
None
(['objective: 175', '  a_0_1=1', '  a_1_1=1', '  a_2_1=1', '  a_3_2=1', '  a_4_1=1', '  a_5_1=1', '  a_6_3=1', '  a_7_2=1', '  a_8_4=1', '  a_9_0=1', '  a_10_4=1', '  a_11_3=1', '  a_12_0=1', '  a_13_3=1', '  a_14_4=1', '  a_15_1=1', '  a_16_0=1', '  a_17_2=1', '  a_18_2=1', '  a_19_2=1', '  a_20_3=1', '  a_21_2=1', '  a_22_0=1', '  a_23_3=1', '  a_24_0=1', '  a_25_4=1', '  a_26_0=1', '  a_27_1=1', '  a_28_3=1', '  a_29_4=1', '  a_30_0=1', '  a_31_4=1', '  a_32_2=1', '  a_33_2=1', '  a_34_1=1', '  a_35_4=1', '  a_36_2

solution for a cost of 167
objective: 167
  a_0_3=1
  a_1_2=1
  a_2_4=1
  a_3_0=1
  a_4_4=1
  a_5_2=1
  a_6_2=1
  a_7_1=1
  a_8_0=1
  a_9_3=1
  a_10_2=1
  a_11_4=1
  a_12_4=1
  a_13_1=1
  a_14_0=1
  a_15_3=1
  a_16_2=1
  a_17_2=1
  a_18_0=1
  a_19_3=1
  a_20_1=1
  a_21_2=1
  a_22_1=1
  a_23_0=1
  a_24_3=1
  a_25_0=1
  a_26_4=1
  a_27_1=1
  a_28_3=1
  a_29_3=1
  a_30_1=1
  a_31_4=1
  a_32_1=1
  a_33_0=1
  a_34_0=1
  a_35_1=1
  a_36_4=1
  a_37_2=1
  a_38_2=1
  a_39_1=1
None
(['objective: 167', '  a_0_3=1', '  a_1_2=1', '  a_2_4=1', '  a_3_0=1', '  a_4_4=1', '  a_5_2=1', '  a_6_2=1', '  a_7_1=1', '  a_8_0=1', '  a_9_3=1', '  a_10_2=1', '  a_11_4=1', '  a_12_4=1', '  a_13_1=1', '  a_14_0=1', '  a_15_3=1', '  a_16_2=1', '  a_17_2=1', '  a_18_0=1', '  a_19_3=1', '  a_20_1=1', '  a_21_2=1', '  a_22_1=1', '  a_23_0=1', '  a_24_3=1', '  a_25_0=1', '  a_26_4=1', '  a_27_1=1', '  a_28_3=1', '  a_29_3=1', '  a_30_1=1', '  a_31_4=1', '  a_32_1=1', '  a_33_0=1', '  a_34_0=1', '  a_35_1=1', '  a_36_4

solution for a cost of 175
objective: 175
  a_0_4=1
  a_1_3=1
  a_2_0=1
  a_3_2=1
  a_4_2=1
  a_5_4=1
  a_6_0=1
  a_7_3=1
  a_8_4=1
  a_9_3=1
  a_10_4=1
  a_11_0=1
  a_12_3=1
  a_13_0=1
  a_14_1=1
  a_15_0=1
  a_16_0=1
  a_17_0=1
  a_18_2=1
  a_19_3=1
  a_20_1=1
  a_21_1=1
  a_22_1=1
  a_23_3=1
  a_24_4=1
  a_25_4=1
  a_26_0=1
  a_27_2=1
  a_28_2=1
  a_29_1=1
  a_30_2=1
  a_31_3=1
  a_32_1=1
  a_33_1=1
  a_34_4=1
  a_35_3=1
  a_36_2=1
  a_37_2=1
  a_38_0=1
  a_39_4=1
None
(['objective: 175', '  a_0_4=1', '  a_1_3=1', '  a_2_0=1', '  a_3_2=1', '  a_4_2=1', '  a_5_4=1', '  a_6_0=1', '  a_7_3=1', '  a_8_4=1', '  a_9_3=1', '  a_10_4=1', '  a_11_0=1', '  a_12_3=1', '  a_13_0=1', '  a_14_1=1', '  a_15_0=1', '  a_16_0=1', '  a_17_0=1', '  a_18_2=1', '  a_19_3=1', '  a_20_1=1', '  a_21_1=1', '  a_22_1=1', '  a_23_3=1', '  a_24_4=1', '  a_25_4=1', '  a_26_0=1', '  a_27_2=1', '  a_28_2=1', '  a_29_1=1', '  a_30_2=1', '  a_31_3=1', '  a_32_1=1', '  a_33_1=1', '  a_34_4=1', '  a_35_3=1', '  a_36_2

solution for a cost of 182
objective: 182
  a_0_0=1
  a_1_0=1
  a_2_1=1
  a_3_1=1
  a_4_2=1
  a_5_4=1
  a_6_1=1
  a_7_2=1
  a_8_1=1
  a_9_0=1
  a_10_1=1
  a_11_0=1
  a_12_2=1
  a_13_3=1
  a_14_3=1
  a_15_2=1
  a_16_4=1
  a_17_3=1
  a_18_1=1
  a_19_1=1
  a_20_2=1
  a_21_3=1
  a_22_3=1
  a_23_1=1
  a_24_4=1
  a_25_0=1
  a_26_4=1
  a_27_4=1
  a_28_2=1
  a_29_2=1
  a_30_4=1
  a_31_0=1
  a_32_3=1
  a_33_4=1
  a_34_0=1
  a_35_3=1
  a_36_0=1
  a_37_3=1
  a_38_4=1
  a_39_2=1
None
(['objective: 182', '  a_0_0=1', '  a_1_0=1', '  a_2_1=1', '  a_3_1=1', '  a_4_2=1', '  a_5_4=1', '  a_6_1=1', '  a_7_2=1', '  a_8_1=1', '  a_9_0=1', '  a_10_1=1', '  a_11_0=1', '  a_12_2=1', '  a_13_3=1', '  a_14_3=1', '  a_15_2=1', '  a_16_4=1', '  a_17_3=1', '  a_18_1=1', '  a_19_1=1', '  a_20_2=1', '  a_21_3=1', '  a_22_3=1', '  a_23_1=1', '  a_24_4=1', '  a_25_0=1', '  a_26_4=1', '  a_27_4=1', '  a_28_2=1', '  a_29_2=1', '  a_30_4=1', '  a_31_0=1', '  a_32_3=1', '  a_33_4=1', '  a_34_0=1', '  a_35_3=1', '  a_36_0

...

solution for a cost of 174
objective: 174
  a_0_1=1
  a_1_2=1
  a_2_1=1
  a_3_3=1
  a_4_2=1
  a_5_1=1
  a_6_0=1
  a_7_0=1
  a_8_1=1
  a_9_2=1
  a_10_0=1
  a_11_1=1
  a_12_0=1
  a_13_4=1
  a_14_3=1
  a_15_3=1
  a_16_1=1
  a_17_4=1
  a_18_0=1
  a_19_0=1
  a_20_3=1
  a_21_4=1
  a_22_2=1
  a_23_4=1
  a_24_3=1
  a_25_3=1
  a_26_3=1
  a_27_1=1
  a_28_4=1
  a_29_0=1
  a_30_2=1
  a_31_0=1
  a_32_2=1
  a_33_3=1
  a_34_1=1
  a_35_2=1
  a_36_4=1
  a_37_4=1
  a_38_2=1
  a_39_0=1
None
(['objective: 174', '  a_0_1=1', '  a_1_2=1', '  a_2_1=1', '  a_3_3=1', '  a_4_2=1', '  a_5_1=1', '  a_6_0=1', '  a_7_0=1', '  a_8_1=1', '  a_9_2=1', '  a_10_0=1', '  a_11_1=1', '  a_12_0=1', '  a_13_4=1', '  a_14_3=1', '  a_15_3=1', '  a_16_1=1', '  a_17_4=1', '  a_18_0=1', '  a_19_0=1', '  a_20_3=1', '  a_21_4=1', '  a_22_2=1', '  a_23_4=1', '  a_24_3=1', '  a_25_3=1', '  a_26_3=1', '  a_27_1=1', '  a_28_4=1', '  a_29_0=1', '  a_30_2=1', '  a_31_0=1', '  a_32_2=1', '  a_33_3=1', '  a_34_1=1', '  a_35_2=1', '  a_36_4

solution for a cost of 173
objective: 173
  a_0_1=1
  a_1_2=1
  a_2_4=1
  a_3_1=1
  a_4_4=1
  a_5_2=1
  a_6_4=1
  a_7_2=1
  a_8_2=1
  a_9_0=1
  a_10_4=1
  a_11_2=1
  a_12_3=1
  a_13_3=1
  a_14_4=1
  a_15_1=1
  a_16_0=1
  a_17_3=1
  a_18_3=1
  a_19_1=1
  a_20_3=1
  a_21_3=1
  a_22_0=1
  a_23_1=1
  a_24_4=1
  a_25_3=1
  a_26_3=1
  a_27_1=1
  a_28_0=1
  a_29_2=1
  a_30_4=1
  a_31_0=1
  a_32_0=1
  a_33_3=1
  a_34_4=1
  a_35_1=1
  a_36_2=1
  a_37_0=1
  a_38_1=1
  a_39_0=1
None
(['objective: 173', '  a_0_1=1', '  a_1_2=1', '  a_2_4=1', '  a_3_1=1', '  a_4_4=1', '  a_5_2=1', '  a_6_4=1', '  a_7_2=1', '  a_8_2=1', '  a_9_0=1', '  a_10_4=1', '  a_11_2=1', '  a_12_3=1', '  a_13_3=1', '  a_14_4=1', '  a_15_1=1', '  a_16_0=1', '  a_17_3=1', '  a_18_3=1', '  a_19_1=1', '  a_20_3=1', '  a_21_3=1', '  a_22_0=1', '  a_23_1=1', '  a_24_4=1', '  a_25_3=1', '  a_26_3=1', '  a_27_1=1', '  a_28_0=1', '  a_29_2=1', '  a_30_4=1', '  a_31_0=1', '  a_32_0=1', '  a_33_3=1', '  a_34_4=1', '  a_35_1=1', '  a_36_2

solution for a cost of 169
objective: 169
  a_0_4=1
  a_1_0=1
  a_2_1=1
  a_3_3=1
  a_4_2=1
  a_5_1=1
  a_6_2=1
  a_7_0=1
  a_8_1=1
  a_9_0=1
  a_10_1=1
  a_11_3=1
  a_12_2=1
  a_13_4=1
  a_14_0=1
  a_15_4=1
  a_16_3=1
  a_17_3=1
  a_18_0=1
  a_19_3=1
  a_20_0=1
  a_21_2=1
  a_22_2=1
  a_23_4=1
  a_24_4=1
  a_25_2=1
  a_26_3=1
  a_27_1=1
  a_28_1=1
  a_29_2=1
  a_30_4=1
  a_31_1=1
  a_32_1=1
  a_33_4=1
  a_34_4=1
  a_35_3=1
  a_36_2=1
  a_37_0=1
  a_38_4=1
  a_39_3=1
None
(['objective: 169', '  a_0_4=1', '  a_1_0=1', '  a_2_1=1', '  a_3_3=1', '  a_4_2=1', '  a_5_1=1', '  a_6_2=1', '  a_7_0=1', '  a_8_1=1', '  a_9_0=1', '  a_10_1=1', '  a_11_3=1', '  a_12_2=1', '  a_13_4=1', '  a_14_0=1', '  a_15_4=1', '  a_16_3=1', '  a_17_3=1', '  a_18_0=1', '  a_19_3=1', '  a_20_0=1', '  a_21_2=1', '  a_22_2=1', '  a_23_4=1', '  a_24_4=1', '  a_25_2=1', '  a_26_3=1', '  a_27_1=1', '  a_28_1=1', '  a_29_2=1', '  a_30_4=1', '  a_31_1=1', '  a_32_1=1', '  a_33_4=1', '  a_34_4=1', '  a_35_3=1', '  a_36_2

solution for a cost of 188
objective: 188
  a_0_2=1
  a_1_3=1
  a_2_3=1
  a_3_1=1
  a_4_1=1
  a_5_2=1
  a_6_1=1
  a_7_0=1
  a_8_0=1
  a_9_0=1
  a_10_2=1
  a_11_4=1
  a_12_0=1
  a_13_4=1
  a_14_2=1
  a_15_0=1
  a_16_4=1
  a_17_4=1
  a_18_3=1
  a_19_3=1
  a_20_2=1
  a_21_0=1
  a_22_2=1
  a_23_0=1
  a_24_2=1
  a_25_2=1
  a_26_1=1
  a_27_0=1
  a_28_4=1
  a_29_3=1
  a_30_4=1
  a_31_4=1
  a_32_1=1
  a_33_0=1
  a_34_1=1
  a_35_4=1
  a_36_3=1
  a_37_3=1
  a_38_3=1
  a_39_1=1
None
(['objective: 188', '  a_0_2=1', '  a_1_3=1', '  a_2_3=1', '  a_3_1=1', '  a_4_1=1', '  a_5_2=1', '  a_6_1=1', '  a_7_0=1', '  a_8_0=1', '  a_9_0=1', '  a_10_2=1', '  a_11_4=1', '  a_12_0=1', '  a_13_4=1', '  a_14_2=1', '  a_15_0=1', '  a_16_4=1', '  a_17_4=1', '  a_18_3=1', '  a_19_3=1', '  a_20_2=1', '  a_21_0=1', '  a_22_2=1', '  a_23_0=1', '  a_24_2=1', '  a_25_2=1', '  a_26_1=1', '  a_27_0=1', '  a_28_4=1', '  a_29_3=1', '  a_30_4=1', '  a_31_4=1', '  a_32_1=1', '  a_33_0=1', '  a_34_1=1', '  a_35_4=1', '  a_36_3

[array([[27, 35, 25, 28, 21, 23, 30, 29, 39, 24, 30, 48, 15, 27, 19, 23,
         26, 29, 26, 22, 43, 31, 39, 40, 27, 35, 30, 37, 20, 27, 33, 30,
         36, 30, 19, 39, 41, 25, 45, 37],
        [27, 22, 36, 26, 33, 40, 23, 44, 21, 22, 26, 32, 31, 41, 42, 40,
         32, 33, 35, 24, 24, 27, 25, 35, 31, 29, 34, 27, 32, 26, 31, 31,
         27, 25, 17, 35, 35, 17, 14, 35],
        [31, 28, 34, 22, 34, 34, 31, 37, 36, 27, 41, 29, 15, 41, 32, 39,
         31, 41, 27, 24, 31, 40, 23, 28, 32, 35, 32, 20, 28, 24, 21, 26,
         33, 26, 27, 12, 22, 17, 17, 26],
        [19, 30, 24, 37, 21, 30, 23, 34, 24, 29, 35, 32, 24, 21, 26, 35,
         31, 27, 51, 34, 39, 40, 27, 28, 39, 35, 30, 30, 28, 34, 40, 32,
         38, 29, 30, 32, 22, 31, 27, 39],
        [19, 30, 35, 32, 27, 35, 40, 33, 24, 33, 23, 41, 23, 23, 28, 32,
         34, 15, 45, 19, 31, 29, 40, 28, 30, 38, 33, 21, 30, 19, 32, 22,
         31, 40, 31, 24, 33, 27, 32, 30]], dtype=int64),
 array([[31, 28, 27, 32, 34, 38, 23, 51, 30, 

In [12]:
#safe 3 arrays in a npz file
#keys: 'jm_mat' for input data
# 'alloc_mat' for labaled output data
# 'solve_stat' for knowledge of sol is optimal or only feasable
np.savez('scheduling_inputdata.npz', jm_mat=np.array(x), alloc_mat=np.array(y),solve_stat=np.array(stat))